In [ ]:
!pip install pythoncrc
!pip install pandas --upgrade
!pip install geemap --upgrade

In [2]:
import ee
import geemap
import os


In [4]:
ee.Authenticate()

In [5]:
ee.Initialize(project='uv-cursogee2025')

#**Cargar Puntos**

In [6]:
pts = ee.FeatureCollection('projects/uv-cursogee2025/assets/PuntosCamaraTrampa')

In [7]:
MMdist = ee.FeatureCollection('projects/gee-extractraster/assets/MacacaMaura_Distribution_2021')

#**Settings**

In [8]:
def func_hyu(image):
    return image.clip(MMdist)

cliptocol = func_hyu


In [9]:
import pandas as pd
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


#**Buffer points**

In [10]:
def bufferPoints(radius, bounds):

    def func_bpc(pt):
        pt = ee.Feature(pt)
        return pt.buffer(radius).bounds()

    return func_bpc

Squares

In [12]:
buffer_250 = pts.map(bufferPoints(250, False))
buffer_500 = pts.map(bufferPoints(500, False))
buffer_2km = pts.map(bufferPoints(707.1, False))
buffer_750 = pts.map(bufferPoints(750, False))
buffer_1000 = pts.map(bufferPoints(1000, False))
buffer_1250 = pts.map(bufferPoints(1250, False))

Round

In [ ]:
rbuffer_250 = pts.map(bufferPoints(250, True))
rbuffer_500 = pts.map(bufferPoints(500, True))
rbuffer_750 = pts.map(bufferPoints(750, True))
rbuffer_1000 = pts.map(bufferPoints(1000, True))
rbuffer_1250 = pts.map(bufferPoints(1250, True))

In [20]:
Map = geemap.Map(basemap='SATELLITE')
Map.centerObject(MMdist,8)

Map.addLayer(buffer_1250, {'color': 'red'}, "1250", opacity=0.25)
Map.addLayer(buffer_1000, {'color': 'orange'}, "1000", opacity=0.25)
Map.addLayer(buffer_750, {'color': 'yellow'}, "750", opacity=0.25)
Map.addLayer(buffer_500, {'color': 'green'}, "500", opacity=0.25)
Map.addLayer(buffer_250,{'color': 'blue'}, "250", opacity=0.25)

Map

Map(center=[-4.6947954738484405, 119.92721030782943], controls=(WidgetControl(options=['position', 'transparen…

# **Proyección**

In [39]:
# Conocer la proyección de los puntos

print(pts.first().geometry().projection().crs().getInfo())

EPSG:4326


#**Tree Height**

In [21]:
TreeHeight = ee.ImageCollection("projects/sat-io/open-datasets/GLAD/GEDI_V27").map(cliptocol)

In [22]:
TreeHeightVisParams = {
    "bands": ["b1"],
    "min":10,
    "max": 50,
    "palette": ['#FFFFFF', '#00ff00']}
Map.addLayer(TreeHeight, TreeHeightVisParams, name="Tree Height")
Map

Map(bottom=134908.0, center=[-4.849469891371024, 119.98019889569545], controls=(WidgetControl(options=['positi…

In [24]:
TH = ee.Image(TreeHeight.mosaic())

In [31]:
#Threshold 10m
# Remap values in TH image.
Forest = TH.where(TH.lte(9), 0).where(TH.gt(9), 1)

In [45]:
forest_params = {'bands': ['b1'], 'min': 0, 'max': 1, 'gamma': 1}
Map.addLayer(Forest, forest_params, "Forest")
Map

Map(bottom=33867.0, center=[-4.384751860236625, 120.05639622166268], controls=(WidgetControl(options=['positio…

In [28]:
# Define the directory path in Google Drive
output_dir = '/content/drive/MyDrive/CursoGEE2025'

# Create the directory if it doesn't exist
if not os.path.exists(output_dir):
    os.makedirs(output_dir)
    print(f"Directory '{output_dir}' created.")
else:
    print(f"Directory '{output_dir}' already exists.")

Directory '/content/drive/MyDrive/CursoGEE2025' created.


In [40]:
# Proyección de pts
pts_crs = pts.first().geometry().projection().crs()
print(f"CRS of pts: {pts_crs.getInfo()}")

# Proyección de TreeHeight
treeheight_crs = TreeHeight.first().projection().crs()
print(f"CRS of TreeHeight: {treeheight_crs.getInfo()}")

# Comparar proyecciones, y reproyectar a la prpyección de pts si TreeHeight tiene diferente proyección
if pts_crs.getInfo() != treeheight_crs.getInfo():
    print("Projections are different. Reprojecting TreeHeight to match pts.")
    TreeHeight = TreeHeight.map(lambda image: image.reproject(crs=pts_crs))
else:
    print("Projections are the same.")

CRS of pts: EPSG:4326
CRS of TreeHeight: EPSG:4326
Projections are the same.


In [41]:
# Saber el tamaño de pixel de TreeHeight
treeheight_scale = TreeHeight.first().projection().nominalScale()
print(f"Scale of TreeHeight: {treeheight_scale.getInfo()} meters")

Nominal scale of TreeHeight: 27.829872698318393 meters


In [35]:
geemap.zonal_stats(
    TreeHeight,
    buffer_2km,
    '/content/drive/MyDrive/CursoGEE2025/MaxTreeHeight2km.csv',
    stat_type="MAXIMUM",
    scale=treeheight_scale,
    crs="EPSG:4326")

Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/CursoGEE2025/MaxTreeHeight2km.csv


In [36]:
geemap.zonal_stats_by_group(
    Forest,
    buffer_2km,
    '/content/drive/MyDrive/CursoGEE2025/Forest2km.csv',
    stat_type="PERCENTAGE",
    decimal_places=2,
    scale=27.83,
    crs="EPSG:4326")

Computing ... 
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/CursoGEE2025/Forest2km.csv


In [ ]:
# Define a list of buffer objects
buffers = [buffer_250, buffer_500, buffer_2km, buffer_750, buffer_1000, buffer_1250]

# Define a list of corresponding output file names
output_files = [
    '/content/drive/MyDrive/CursoGEE2025/Forest250.csv',
    '/content/drive/MyDrive/CursoGEE2025/Forest500.csv',
    '/content/drive/MyDrive/CursoGEE2025/Forest2km.csv',
    '/content/drive/MyDrive/CursoGEE2025/Forest750.csv',
    '/content/drive/MyDrive/CursoGEE2025/Forest1000.csv',
    '/content/drive/MyDrive/CursoGEE2025/Forest1250.csv',
]

# Iterate through buffers and calculate zonal statistics
for i, buffer in enumerate(buffers):
    geemap.zonal_stats_by_group(
        Forest,
        buffer,
        output_files[i],
        stat_type="SUM",
        decimal_places=2,
        scale=30,
        tile_scale=16,
        crs="EPSG:4326"
    )

#**Dynamic World**

In [ ]:
startDate = '2020-01-01';
timeIntervalYears = 4;

endDate = ee.Date(startDate).advance(timeIntervalYears, 'years')

In [ ]:
dw = ee.ImageCollection('GOOGLE/DYNAMICWORLD/V1').map(cliptocol);

dwClassInfo = {
  0: {'name': 'water', 'color': '#419BDF'}, # added quotes around name and color
  1: {'name': 'trees', 'color': '#397D49'}, # added quotes around name and color
  2: {'name': 'grass', 'color': '#88B053'},  # added quotes around name and color
  3: {'name': 'flooded_vegetation', 'color': '#7A87C6'}, # added quotes around name and color
  4: {'name': 'crops', 'color': '#E49635'}, # added quotes around name and color
  5: {'name': 'shrub_and_scrub', 'color': '#DFC35A'}, # added quotes around name and color
  6: {'name': 'built', 'color': '#C4281B'}, # added quotes around name and color
  7: {'name': 'bare', 'color': '#A59B8F'}, # added quotes around name and color
  8: {'name': 'snow_and_ice', 'color': '#B39FE1'}, # added quotes around name and color
}

In [ ]:
def func_blj (v):
    return ee.Dictionary(v).get(prop)
    return ee.Dictionary(dict).values().map(
        lambda v: ee.Dictionary(v).get(prop)
    )
    return ee.Dictionary(dict).values().map(
func_blj)


In [ ]:
def getClassProperty(dict, prop):

    def func_ovd (v):
        return ee.Dictionary(v).get(prop)
    return ee.Dictionary(dict).values().map(
        lambda v: ee.Dictionary(v).get(prop)
    )
    return ee.Dictionary(dict).values().map(
func_ovd)


In [ ]:
probabilityBands = getClassProperty(dwClassInfo, 'name');
dwClassPalette = getClassProperty(dwClassInfo, 'color');
dwVisParams = {"min": 0, "max": 8, "palette": dwClassPalette.getInfo()};


In [ ]:
dwTimeInterval = dw.filter(ee.Filter.date(startDate, endDate))

In [ ]:
dwTimeSeries = dwTimeInterval.select(probabilityBands)

In [ ]:
meanProbability = dwTimeSeries.reduce(ee.Reducer.mean())

In [ ]:
dwClassComposite = meanProbability.toArray().arrayArgmax().arrayGet(0).rename("label")

In [ ]:
region = MMdist.geometry()

In [ ]:
geemap.ee_export_image_to_asset(
image=dwClassComposite,
description='DW',
assetId='projects/uv-cursogee2025/assets/DW2023',
region=region,
scale=10,
crs="EPSG:4326",
maxPixels=10000000000
)


In [ ]:
geemap.ee_export_image_to_drive(
    Forest, description="landsat", folder="export", scale=30
)

In [ ]:
dwClassComposite = dwClassComposite.remap([0, 1, 2, 3, 4, 5, 6, 7, 8], ["Water", "Trees", "Grass", "Flooded_Vegetation", "Agriculture", "Shrub", "Built", "Bare", "Snow_Ice"], bandName="label")

In [ ]:
region = Map.user_roi
pts1= buffer_750.filterBounds(region)
dwStats = "/content/drive/MyDrive/CursoGEE2025/DW.tif"

In [ ]:
dwStats = ee.Image('projects/uv-cursogee2025/assets/DW2023')

In [ ]:
# Assuming dwStats is the ee.Image you want to analyze

# For buffer_250
geemap.zonal_stats_by_group(
    dwCrop,
    buffer_250,
    '/content/drive/MyDrive/CursoGEE2025/crop250.csv', # Changed output file name
    stat_type="PERCENTAGE",
    decimal_places=2,
    scale=10,
    tile_scale=16,
    crs="EPSG:4326")

Computing ... 
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/Moor macaque survey 2023/Covariates Occupancy Models/crop250.csv


In [ ]:
# For buffer_500
geemap.zonal_stats_by_group(
    dwCrop,
    buffer_500,
    '/content/drive/MyDrive/CursoGEE2025/crop500.csv', # Changed output file name
    stat_type="PERCENTAGE",
    decimal_places=2,
    scale=10,
    tile_scale=16,
    crs="EPSG:4326")

Computing ... 
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/Moor macaque survey 2023/Covariates Occupancy Models/crop500.csv


In [ ]:
# For buffer_750
geemap.zonal_stats_by_group(
    dwCrop,
    buffer_750,
    '/content/drive/MyDrive/CursoGEE2025/crop750.csv', # Changed output file name
    stat_type="PERCENTAGE",
    decimal_places=2,
    scale=10,
    tile_scale=16,
    crs="EPSG:4326")

Computing ... 
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/Moor macaque survey 2023/Covariates Occupancy Models/crop750.csv


In [ ]:
# For buffer_1000
geemap.zonal_stats_by_group(
    dwCrop,
    buffer_1000,
    '/content/drive/MyDrive/CursoGEE2025/crop1000.csv', # Changed output file name
    stat_type="PERCENTAGE",
    decimal_places=2,
    scale=10,
    tile_scale=16,
    crs="EPSG:4326")

Computing ... 
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/Moor macaque survey 2023/Covariates Occupancy Models/crop1000.csv


In [ ]:
geemap.zonal_stats_by_group(
    dwCrop,
    buffer_1250,
    '/content/drive/MyDrive/CursoGEE2025/crop1250.csv',
    stat_type="PERCENTAGE",
    decimal_places=2,
    scale=10,
    tile_scale=16,
    crs="EPSG:4326")

Computing ... 
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/Moor macaque survey 2023/Covariates Occupancy Models/crop1250.csv


In [ ]:
# For buffer_2km
geemap.zonal_stats_by_group(
    dwCrop,
    buffer_2km,
    '/content/drive/MyDrive/CursoGEE2025/crop2km.csv', # Changed output file name
    stat_type="PERCENTAGE",
    decimal_places=2,
    scale=10,
    tile_scale=16,
    crs="EPSG:4326")

Computing ... 
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/Moor macaque survey 2023/Covariates Occupancy Models/crop2km.csv


#**NDVI**

##Image

In [ ]:
# Import the Landsat 8 TOA image collection.
l8 = ee.ImageCollection('LANDSAT/LC08/C02/T1').map(cliptocol)\
.filterDate('2023-03-17', '2023-03-21')


In [ ]:
image = ee.Algorithms.Landsat.simpleComposite(l8)

In [ ]:
# Compute the Normalized Difference Vegetation Index (NDVI).
nir = image.select('B5')
red = image.select('B4')
ndvi = nir.subtract(red).divide(nir.add(red)).rename('NDVI')

In [ ]:
ndvi = image.normalizedDifference(['B5', 'B4']).rename('NDVI')

In [ ]:
# Display the result.

ndviParams = {'min': -1, 'max': 1, 'palette': ['blue', 'white', 'green']}
Map.addLayer(ndvi, ndviParams, 'NDVI image')

In [ ]:
# Define a list of buffer objects
buffers = [buffer_250, buffer_500, buffer_2km, buffer_750, buffer_1000, buffer_1250]

# Define a list of corresponding output file names
output_files = [
    '/content/drive/MyDrive/CursoGEE2025/NDVI250p.csv',
    '/content/drive/MyDrive/CursoGEE2025/NDVI500p.csv',
    '/content/drive/MyDrive/CursoGEE2025/NDVI2kmp.csv',
    '/content/drive/MyDrive/CursoGEE2025/NDVI750p.csv',
    '/content/drive/MyDrive/CursoGEE2025/NDVI1000p.csv',
    '/content/drive/MyDrive/CursoGEE2025/NDVI1250p.csv',
]

# Iterate through buffers and calculate zonal statistics
for i, buffer in enumerate(buffers):
    geemap.zonal_stats(
        ndvi,
        buffer,
        output_files[i],
        stat_type="MEAN",
        decimal_places=2,
        scale=30,
        tile_scale=16,
        crs="EPSG:4326"
    )

Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/Moor macaque survey 2023/Covariates Occupancy Models/NDVI/MEAN/NDVI250p.csv
Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/Moor macaque survey 2023/Covariates Occupancy Models/NDVI/MEAN/NDVI500p.csv
Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/Moor macaque survey 2023/Covariates Occupancy Models/NDVI/MEAN/NDVI2kmp.csv
Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/Moor macaque survey 2023/Covariates Occupancy Models/NDVI/MEAN/NDVI750p.csv
Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/Moor macaque survey 2023/Covariates Occupancy Models/NDVI/MEAN/NDVI1000p.csv
Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/Moor ma

In [ ]:
# Define a list of buffer objects
buffers = [buffer_250, buffer_500, buffer_2km, buffer_750, buffer_1000, buffer_1250]

# Define a list of corresponding output file names
output_files = [
    '/content/drive/MyDrive/CursoGEE2025/NDVI250v.csv',
    '/content/drive/MyDrive/CursoGEE2025/NDVI500v.csv',
    '/content/drive/MyDrive/CursoGEE2025/NDVI2kmv.csv',
    '/content/drive/MyDrive/CursoGEE2025/NDVI750v.csv',
    '/content/drive/MyDrive/CursoGEE2025/NDVI1000v.csv',
    '/content/drive/MyDrive/CursoGEE2025/NDVI1250v.csv',
]

# Iterate through buffers and calculate zonal statistics
for i, buffer in enumerate(buffers):
    geemap.zonal_stats(
        ndvi,
        buffer,
        output_files[i],
        stat_type="VARIANCE",
        decimal_places=2,
        scale=30,
        tile_scale=16,
        crs="EPSG:4326"
    )

#**Human Footprint Index**

In [46]:
HFI2019 = ee.Image('projects/gee-extractraster/assets/HFI2020')

In [47]:
# prompt: get crs of pts feature collection

print(pts.first().geometry().projection().crs().getInfo())

EPSG:4326


In [48]:
# Reproject HFI2019 to the CRS of buffer_2km
HFI2019_reprojected = HFI2019.reproject(
    crs="EPSG:4326",
    scale=HFI2019.projection().nominalScale() # Keep the original resolution
).clip(MMdist)


# Print the CRS of the reprojected HFI2019 for verification
print('CRS of HFI2019_reprojected:', HFI2019_reprojected.projection().crs().getInfo())


CRS of HFI2019_reprojected: EPSG:4326


In [49]:
geemap.zonal_stats(
    HFI2019_reprojected,
    buffer_2km,
    '/content/drive/MyDrive/CursoGEE2025/HFI2020_2km.csv',
    stat_type="MEAN",
    scale=30,
    crs="EPSG:4326",
    decimal_places=2
    )

Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/CursoGEE2025/HFI2020_2km.csv


Extract values as raster

In [50]:
reduced = HFI2019.reduceRegions(
    collection= buffer_2km,
    reducer=ee.Reducer.mean(),
    scale=30
)

In [51]:
raster = reduced.reduceToImage(
    properties=['mean'],  # Property containing the mean values
    reducer=ee.Reducer.first()
)

In [ ]:
# prompt: esport raster to drive

geemap.ee_export_image_to_drive(
    raster,
    description='HumanFootprintIndex_2km_raster',  # Name of the export task
    folder='earthengine/Rasters',  # Folder in your Google Drive
    scale=30,  # Resolution of the exported image
    region=buffer_2km.geometry(), # Export bounds based on the buffer geometry
    fileFormat='GeoTIFF', # Output file format
    maxPixels=10000000000
)

In [52]:
# prompt: add "raster" to the map and print the map
Map = geemap.Map(basemap="Esri.WorldImagery")
Map.addLayer(raster, {}, "HFIr")
Map

Map(center=[0, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], position='topright', transp…

In [ ]:
# Define a list of buffer objects
buffers = [buffer_250, buffer_500, buffer_2km, buffer_750, buffer_1000, buffer_1250]

# Define a list of corresponding output file names
output_files = [
    '/content/drive/MyDrive/CursoGEE2025/HFI2020250.csv',
    '/content/drive/MyDrive/CursoGEE2025/HFI2020500.csv',
    '/content/drive/MyDrive/CursoGEE2025/HFI20202km.csv',
    '/content/drive/MyDrive/CursoGEE2025/HFI2020750.csv',
    '/content/drive/MyDrive/CursoGEE2025/HFI20201000.csv',
    '/content/drive/MyDrive/CursoGEE2025/HFI20201250.csv',
]

# Iterate through buffers and calculate zonal statistics
for i, buffer in enumerate(buffers):
    geemap.zonal_stats(
        HFI2019,
        buffer,
        output_files[i],
        stat_type="MEAN",
        decimal_places=2,
        scale=30,
        tile_scale=16,
        crs="EPSG:4326"
    )

Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/Moor macaque survey 2023/Covariates Occupancy Models/Human Footprint Index/HFI2020250.csv
Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/Moor macaque survey 2023/Covariates Occupancy Models/Human Footprint Index/HFI2020500.csv
Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/Moor macaque survey 2023/Covariates Occupancy Models/Human Footprint Index/HFI20202km.csv
Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/Moor macaque survey 2023/Covariates Occupancy Models/Human Footprint Index/HFI2020750.csv
Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /content/drive/MyDrive/Moor macaque survey 2023/Covariates Occupancy Models/Human Footprint Index/HFI20201000.csv
Computing statistics ...
Generating URL

#**Elevation and Slope**

In [ ]:
# Import the MERIT global elevation dataset.
elev = ee.Image('MERIT/DEM/v1_0_3');

In [ ]:
# Calculate slope from the DEM.
slope = ee.Terrain.slope(elev);

In [ ]:
# Concatenate elevation and slope as two bands of an image.
topo = ee.Image.cat(elev, slope)

In [ ]:
geemap.zonal_stats(
    elev,
    buffer_250,
    '/content/drive/MyDrive/CursoGEE2025/Slope50.csv',
    stat_type="MEAN",
    decimal_places=2,
    scale=92.77,
    tile_scale=16,
    crs="EPSG:4326")

In [ ]:
geemap.zonal_stats(
    slope,
    buffer_250,
    '/content/drive/MyDrive/CursoGEE2025/Slope50.csv',
    stat_type="MEAN",
    decimal_places=2,
    scale=92.77,
    tile_scale=16,
    crs="EPSG:4326")